## Импорт библиотек, тест запуска

In [16]:
import requests
from bs4 import BeautifulSoup

headers = {
    'user-agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_11_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/53.0.2785.143 Safari/537.36'
    }

In [3]:
url = 'https://shikimori.one/animes/page/1'
response = requests.get(url, headers=headers, timeout=5)
soup = BeautifulSoup(response.text, 'lxml')

soup

<!DOCTYPE html>
<html data-color-mode="light"><head><meta charset="utf-8"/><meta content="IE=edge,chrome=1" http-equiv="X-UA-Compatible"/><meta content="width=device-width, initial-scale=1.0" name="viewport"/><link href="/favicon.ico" rel="icon" type="image/x-icon"/><link href="/favicons/favicon-16x16.png" rel="icon" sizes="16x16" type="image/png"/><link href="/favicons/favicon-32x32.png" rel="icon" sizes="32x32" type="image/png"/><link href="/favicons/favicon-96x96.png" rel="icon" sizes="96x96" type="image/png"/><link href="/favicons/favicon-192x192.png" rel="icon" sizes="192x192" type="image/png"/><link href="/favicons/manifest.json" rel="manifest"/><link href="/favicons/apple-touch-icon-57x57.png" rel="apple-touch-icon" sizes="57x57"/><link href="/favicons/apple-touch-icon-60x60.png" rel="apple-touch-icon" sizes="60x60"/><link href="/favicons/apple-touch-icon-72x72.png" rel="apple-touch-icon" sizes="72x72"/><link href="/favicons/apple-touch-icon-76x76.png" rel="apple-touch-icon" siz

## Получение ссылок всех тайтлов

In [5]:
from time import sleep
import openpyxl
new_workbook = openpyxl.Workbook()
new_sheet = new_workbook.active
new_sheet.title = "Anime Links"

# Заголовок таблицы
header = ['Значение p', 'Ссылка на аниме']
new_sheet.append(header)

for p in range(1, 650):
    url = f'https://shikimori.one/animes/page/{p}'
    response = requests.get(url, headers=headers)
    soup = BeautifulSoup(response.text, 'lxml')
    anime_links = soup.findAll('article')
    
    for title in anime_links:
        link = title.find('a').get('href')
        row_data = [p, link]
        new_sheet.append(row_data)  # Записываем данные в файл
    
    if p % 10 == 0:
        print(p)
        sleep(1)
    
    if p % 50 == 0:
        sleep(60)

# Сохраняем новый файл
new_workbook.save('anime_links.xlsx')

10
20
30
40
50
60
70
80
90
100
110
120
130
140
150
160
170
180
190
200
210
220
230
240
250
260
270
280
290
300
310
320
330
340
350
360
370
380
390
400
410
420
430
440
450
460
470
480
490
500
510
520
530
540
550
560
570
580
590
600
610
620
630
640


## Тест кода для парсинга одного выбранного тайтла

In [26]:
import re

data = []

url = 'https://shikimori.one/animes/49613-chiyu-mahou-no-machigatta-tsukaikata'#ВЫБРАННЫЙ ТАЙТЛ
soup = requests.get(url, headers=headers, timeout=5)
soup = BeautifulSoup(soup.text, 'lxml')

anime_name = soup.find('header', class_='head').text.split('/')[0][:-1] #название

info_list = soup.select('.c-info-left .block .line-container') # список парметров левого блока

anime_type = next((i.text[7:-2] for i in info_list if 'Тип' in str(i)), 'Не указано') # Тип
episodes = next((i.text.split(':')[1][1:-2] for i in info_list if "Эпизоды" in str(i)), 'Не указано') # Кол-вл эпизодов
episode_length = next((i.text.split(':')[1][1:-3] for i in info_list if 'Длительность эпизода:' in str(i)), 'Не указано') # Длина эпизода
status = next((i.find('span', class_='b-anime_status_tag')['data-text'] for i in soup.select('.c-info-left .block .line-container') if 'Статус' in str(i)), 'Не указано')
genres = next((re.findall('[А-ЯЁ][а-яё]*', i.text)[1:] for i in info_list if "Жанр" in str(i)), 'Не указано')
themes = [theme.text for i in info_list if 'Тем' in str(i) for theme in i.findAll('span', class_='genre-ru')]
age_limit = next((i.text.split(':')[1][1:-2] for i in info_list if 'Рейтинг' in str(i)), 'Не указано')

studios_list = soup.select('.c-info-right .block')

# Инициализируем пустой список для хранения названий студий
studios = []

# Перебираем блоки в studios_list
for block in studios_list:
    # Ищем блок с заголовком "Студии"
    studios_block = block.find('div', class_='subheadline')
    
    # Если такой блок найден и он содержит "Студии", обрабатываем информацию о студиях
    if studios_block and 'Студии' in studios_block.text:
        # Находим все теги <a> внутри блока с информацией о студиях
        studio_links = block.find_all('a', class_='b-tag')
        
        # Добавляем названия студий в список
        studios.extend([link.text.strip() for link in studio_links])

# Если список студий все еще пуст, пытаемся использовать второй способ
if not studios:
    studio_block = soup.find('div', class_='c-info-right')
    if studio_block:
        string = str(studio_block)
        start = string.find('Аниме студии')
        
        # Проверяем, что строка найдена
        if start != -1:
            result = string[start:]
            new_result = result.split('">')[0]
            studio = new_result[13:]
            studios.append(studio.strip())




authors_link = url + '/staff'
authors_soup = requests.get(authors_link, headers=headers, timeout=5)
authors_soup = BeautifulSoup(authors_soup.text, 'lxml')
# Найти все элементы с классом 'name-ru' (русские имена)
names_elements = authors_soup.find_all(class_='name-ru')

# Извлечь имена и создать список
authors_string = [name.get_text() for name in names_elements]

# Преобразовать список в строку
authors_string = ', '.join(authors_string)



related_link = url + '/related'
related_soup = requests.get(related_link, headers=headers, timeout=5)
related_soup = BeautifulSoup(related_soup.text, 'lxml')

related_list = []

# Find all items with class "b-db_entry-variant-list_item"
items = related_soup.find_all(class_='b-db_entry-variant-list_item')

for item in items:
    # Find the nested element with class "line"
    line_element = item.find(class_='line')

    # Find the value element within the "line" element
    value_element = line_element.find(class_='value')

    # Find the first div with class "b-tag" within the value element
    b_tag_element = value_element.find('div', class_='b-tag')

    # Extract the text content of the "b-tag" element and append to the result list
    if b_tag_element:
        related_list.append(b_tag_element.get_text(strip=True))




# Найти все элементы <div> с классом "b-text_with_paragraphs"
description_elements = soup.find_all('div', class_='b-text_with_paragraphs')

# Используйте регулярные выражения для извлечения текста и исправления проблемы с именами персонажей
for description_element in description_elements:
    # Извлечение текста и замена ссылок на имена персонажей
    description_text = re.sub(r'<a [^>]*>(.*?)<\/a>', r'\1', str(description_element))

    # Другие необходимые обработки, например, удаление HTML-тегов
    description = BeautifulSoup(description_text, 'html.parser').get_text(strip=True)


characters_link = url + '/characters'
characters_soup = requests.get(characters_link, headers=headers, timeout=5)
characters_soup = BeautifulSoup(characters_soup.text, 'lxml')

# Найти div с классом cc-characters
characters_div = characters_soup.find('div', class_='cc-characters')
seiyu_list = []
# Если такой div найден, продолжить парсинг
if characters_div:
    # Найти все теги article в пределах блока cc-characters
    character_articles = characters_div.find_all('article', class_='c-character')

    # Проходим по каждому тегу и извлекаем ссылку на сейю
    for article in character_articles:
        character_name = article.find('span', class_='name-ru').text  # Имя персонажа на русском
        seiyu_link = article.find('a', class_='cover')['href'] + '/seyu'  # Ссылка на сейю

        seiyu_soup = requests.get(seiyu_link, headers=headers, timeout=5)
        seiyu_soup = BeautifulSoup(seiyu_soup.text, 'lxml')

        # Найти div с классом cc-6
        seiyu_div = seiyu_soup.find('div', class_='cc-6')

        # Если такой div найден, продолжить парсинг
        if seiyu_div:
            # Найти все теги article в пределах блока cc-6
            seiyu_articles = seiyu_div.find_all('article', class_='c-person')

            # Проходим по каждому тегу и извлекаем информацию о сейю
            for article in seiyu_articles:
                seiyu_name_element = article.find('span', class_='name-ru')
                role_element = article.find('span', class_='role')

                if seiyu_name_element and role_element:
                    seiyu_name = seiyu_name_element.text  # Имя сейю
                    role = role_element.text.strip()  # Роль сейю (без лишних пробелов)

                    # Проверяем, является ли роль "Сэйю" без дополнительных приписок
                    if role == 'Сэйю':
                        seiyu_list.append(seiyu_name)

        else:
            print(f"Не удалось найти блок cc-6 на странице сейю: {seiyu_link}")

    # Выводим имена сейю через запятую
    seiyu_string = ', '.join(seiyu_list)
else:
    print("Не удалось найти блок cc-characters в HTML.")


score = soup.find('div', class_='text-score').text
digits_only = re.sub(r'\D', '', score)
rate = digits_only[:1] + '.' + digits_only[1:]


data.append([anime_name, anime_type, episodes, episode_length, status, genres, themes, age_limit, studios, authors_string, related_list, description, seiyu_string, rate])
print(data)


[['Неправильный способ использования исцеляющей магии', 'TV Сериал', '10 / 13', '23 мин', 'онгоинг', ['Экшен', 'Фэнтези'], ['Исэкай'], 'PG-13', ['Shin-Ei', 'Add'], 'Такахидэ Огата, Дзюн Мураяма, Кэн Найто, Манами Идзумида, Хироки Мацунага, Аяка Мотида, Ёсиаки Камэда, Тиэми Киси, Масаёри Коминэ, Кадзуаки Макида, Ако Накадзава, Такэси Нэдзу, Кэндзи Танабэ, Маюми Ватанабэ, Масааки Хино, Ясумаса Кояма, Юити Имаидзуми, Эмико Идзима, Сюнсукэ Мацуда, Макото Накамура, Акихиро Нарита, Садахико Сакамаки, Сёго Ясукава, Хироми Коминэ, Хитоси Фудзима, Сэйма Кондо, Кохэй Ямамото, Сатоси Арима, Масаси Хираяма, Манабу Курода, Юки Намики, Косукэ Сюкува, Аса Суэхира, Нобору Сугияма, Кадзухиро Танака, Масахидэ Цудзи, Масаки Ямада, Кадзуо Симидзу, Ямато Сого, Хитоси Сугиура, Хироси Такано, Кодзи Хирокава, Като Сигэру, Май Кавасима, Норихиро Куросава, Сёдзи Осуга, Хисато Усуи, Такааки Исияма, Линлин Чэнь, Цуёси Итики, Саё Сугияма, Акира Такахаси, Сяочуань Чжао, Лукас Альмейда, Аарон Робертс, Масаюки Эгами,

## Код основного автоматизированного парсинга

In [55]:
import re
from time import sleep
import openpyxl
import requests
from bs4 import BeautifulSoup

# Загрузка существующего Excel-файла с ссылками на тайтлы
existing_workbook = openpyxl.load_workbook('data/anime_links.xlsx')
existing_sheet = existing_workbook.active

# Получение значений из второго столбца (второй столбец имеет индекс 1)
urls_column = existing_sheet['B']  # Здесь B - это буква столбца

data = [] # Пустой списиок. Будущей датафрейм


for index, url_cell in enumerate(urls_column, start=1):  # Начинаем с индекса 1, так как первая ячейка заголовка пропущена
    url = url_cell.value  # Получаем значение URL из ячейки
    sleep(1)
    print(f"Элемент {index}: {url}")

    #Получение супа страницы тайтла
    try:
        soup = requests.get(url, headers=headers, timeout=5)
        soup = BeautifulSoup(soup.text, 'lxml')
    except:
        print(f'Не удалось получить суп для {url}')

    #Получение имени тайтла
    try:
        anime_name = soup.find('header', class_='head').text.split('/')[0][:-1]
    except:
        anime_name = 'Не смог'
        print(f'Не смог получить имя тайтла {url}')

    #Получение списка параметров левого блока
    try:
        info_list = soup.select('.c-info-left .block .line-container')
    except:
        print(f'Не смог получить характеристики левого блока для {url}')

    #Получение типа тайтла
    try:
        anime_type = next((i.text[7:-2] for i in info_list if 'Тип' in str(i)), 'Не указано') 
    except:
        anime_type = 'Не смог'
        print(f'Не смог получить тип для тайтла {url}')

    #Получение количества эпизодов тайтла
    try:
        episodes = next((i.text.split(':')[1][1:-2] for i in info_list if "Эпизоды" in str(i)), 'Не указано')
    except:
        episodes = 'Не смог'
        print(f'Не смог получить количество эпизодов для тайтла {url}')

    #Получение длины каждого эпизода тайтла
    try:
        episode_length = next((i.text.split(':')[1][1:-3] for i in info_list if 'Длительность эпизода:' in str(i)), 'Не указано')
    except:
        episode_length = 'Не смог'
        print(f'Не смог получить длину эпизодов для тайтла {url}')

    #Получение статуса тайтла
    try:
        status = next((i.find('span', class_='b-anime_status_tag')['data-text'] for i in soup.select('.c-info-left .block .line-container') if 'Статус' in str(i)), 'Не указано')
    except:
        status = 'Не смог'
        print(f'Не смог получить статус тайтла {url}')

    #Получение списка жанров тайтла
    try:
        genres = next((re.findall('[А-ЯЁ][а-яё]*', i.text)[1:] for i in info_list if "Жанр" in str(i)), 'Не указано')
    except:
        genres = 'Не смог'
        print(f'Не смог получить список жанров для тайтла {url}')

    #Получение списка тем тайтла
    try:
        themes = [theme.text for i in info_list if 'Тем' in str(i) for theme in i.findAll('span', class_='genre-ru')]
    except:
        themes = 'Не смог'
        print(f'Не смог получить список тем для тайтла {url}')

    #Получение возрастного ограничения тайтла
    try:
        age_limit = next((i.text.split(':')[1][1:-2] for i in info_list if 'Рейтинг' in str(i)), 'Не указано')
    except:
        age_limit = 'Не смог'
        print(f'Не смог получить возрастное ограничение для тайтла {url}')


    #Получение студии или списка студий, если их несколько
    try:
        studios_list = soup.select('.c-info-right .block')
        # Инициализируем пустой список для хранения названий студий
        studios = []

        # Перебираем блоки в studios_list
        for block in studios_list:
            # Ищем блок с заголовком "Студии"
            studios_block = block.find('div', class_='subheadline')
        
            # Если такой блок найден и он содержит "Студии", обрабатываем информацию о студиях
            if studios_block and 'Студии' in studios_block.text:
                # Находим все теги <a> внутри блока с информацией о студиях
                studio_links = block.find_all('a', class_='b-tag')
            
                # Добавляем названия студий в список
                studios.extend([link.text.strip() for link in studio_links])

        # Если список студий все еще пуст, пытаемся использовать второй способ
        if not studios:
            studio_block = soup.find('div', class_='c-info-right')
            if studio_block:
                string = str(studio_block)
                start = string.find('Аниме студии')
                
                # Проверяем, что строка найдена
                if start != -1:
                    result = string[start:]
                    new_result = result.split('">')[0]
                    studio = new_result[13:]
                    studios.append(studio.strip())
    except:
        studios = 'Не смог'
        print(f'Не смог получить студию/студии для тайтла {url}')


    #Получение строки авторов(стафа) тайтла
    try:
        authors_link = url + '/staff'
        authors_soup = requests.get(authors_link, headers=headers, timeout=5)
        authors_soup = BeautifulSoup(authors_soup.text, 'lxml')
        # Найти все элементы с классом 'name-ru' (русские имена)
        names_elements = authors_soup.find_all(class_='name-ru')

        # Извлечь имена и создать список
        authors_string = [name.get_text() for name in names_elements]

        # Преобразовать список в строку
        authors_string = ', '.join(authors_string)
    except:
        authors_string = 'Не смог'
        print(f'Не смог получить строку(список) авторов(стафа) для тайтла {url}')


    #Получение информации о наличие связанных произведений(тайтлы, фильмы, овы, манга, ранобе, новеллы и т.д.)
    try:
        related_link = url + '/related'
        related_soup = requests.get(related_link, headers=headers, timeout=5)
        related_soup = BeautifulSoup(related_soup.text, 'lxml')

        related_list = []

        items = related_soup.find_all(class_='b-db_entry-variant-list_item')

        for item in items:
            line_element = item.find(class_='line')

            value_element = line_element.find(class_='value')

            b_tag_element = value_element.find('div', class_='b-tag')

            if b_tag_element:
                related_list.append(b_tag_element.get_text(strip=True))
    except:
        related_list = 'Не смог'
        print(f'Не смог получить информацию о смежных произведениях для тайтла {url}')


    #Получение текстового описания тайтла
    try:
        description_elements = soup.find_all('div', class_='b-text_with_paragraphs')

        # Используйте регулярные выражения для извлечения текста
        for description_element in description_elements:
            # Извлечение текста и замена ссылок на имена персонажей
            description_text = re.sub(r'<a [^>]*>(.*?)<\/a>', r'\1', str(description_element))

            # Другие необходимые обработки, например, удаление HTML-тегов
            description = BeautifulSoup(description_text, 'html.parser').get_text(strip=True)
    except:
        description = 'Не смог'
        print(f'Не смог получить описание для тайтла {url}')


    #Получение строки(списка) сейю главных персонажей тайтла
    #Получение информации о главных персонажах тайтла
    try:
        characters_link = url + '/characters'
        characters_soup = requests.get(characters_link, headers=headers, timeout=5)
        characters_soup = BeautifulSoup(characters_soup.text, 'lxml')

        # Найти div с классом cc-characters
        characters_div = characters_soup.find('div', class_='cc-characters')
        seiyu_list = []
        # Если такой div найден, продолжить парсинг
        if characters_div:
            # Найти все теги article в пределах блока cc-characters
            character_articles = characters_div.find_all('article', class_='c-character')

            # Проходим по каждому тегу и извлекаем ссылку на сейю
            for article in character_articles:
                character_name = article.find('span', class_='name-ru').text  # Имя персонажа на русском
                seiyu_link = article.find('a', class_='cover')['href'] + '/seyu'  # Ссылка на сейю

                seiyu_soup = requests.get(seiyu_link, headers=headers, timeout=5)
                seiyu_soup = BeautifulSoup(seiyu_soup.text, 'lxml')

                # Найти div с классом cc-6
                seiyu_div = seiyu_soup.find('div', class_='cc-6')

                # Если такой div найден, продолжить парсинг
                if seiyu_div:
                    # Найти все теги article в пределах блока cc-6
                    seiyu_articles = seiyu_div.find_all('article', class_='c-person')

                    # Проходим по каждому тегу и извлекаем информацию о сейю
                    for article in seiyu_articles:
                        seiyu_name_element = article.find('span', class_='name-ru')
                        role_element = article.find('span', class_='role')

                        if seiyu_name_element and role_element:
                            seiyu_name = seiyu_name_element.text  # Имя сейю
                            role = role_element.text.strip()  # Роль сейю (без лишних пробелов)

                            # Проверяем, является ли роль "Сэйю" без дополнительных приписок. Сделано для удаления всех иноязычных сейю
                            if role == 'Сэйю':
                                seiyu_list.append(seiyu_name)

                else:
                    print(f"Не удалось найти ОДГОГО из сейю, а именно: {seiyu_link} для тайтла {url}")            

            # Выводим имена сейю через запятую
            seiyu_string = ', '.join(seiyu_list)
        else:
            print(f"Не удалось найти блок cc-characters в HTML для тайтла {url}")

        if len(seiyu_list) == 0:
            print('Скорее всего это ONA тайтл, попытка найти CN Сэйю')
            # Найти все теги article в пределах блока cc-characters
            character_articles = characters_div.find_all('article', class_='c-character')

            # Проходим по каждому тегу и извлекаем ссылку на сейю
            for article in character_articles:
                character_name = article.find('span', class_='name-ru').text  # Имя персонажа на русском
                seiyu_link = article.find('a', class_='cover')['href'] + '/seyu'  # Ссылка на сейю

                seiyu_soup = requests.get(seiyu_link, headers=headers, timeout=5)
                seiyu_soup = BeautifulSoup(seiyu_soup.text, 'lxml')

                # Найти div с классом cc-6
                seiyu_div = seiyu_soup.find('div', class_='cc-6')

                # Если такой div найден, продолжить парсинг
                if seiyu_div:
                    # Найти все теги article в пределах блока cc-6
                    seiyu_articles = seiyu_div.find_all('article', class_='c-person')

                    # Проходим по каждому тегу и извлекаем информацию о сейю
                    for article in seiyu_articles:
                        seiyu_name_element = article.find('span', class_='name-ru')
                        role_element = article.find('span', class_='role')

                        if seiyu_name_element and role_element:
                            seiyu_name = seiyu_name_element.text  # Имя сейю
                            role = role_element.text  # Роль сейю (без лишних пробелов)

                            # Проверяем, является ли роль "Сэйю" без дополнительных приписок. Сделано для удаления всех иноязычных сейю
                            if role == 'Сэйю (CH)':
                                seiyu_list.append(seiyu_name)

                else:
                    print(f"Не удалось найти китайского сейю, а именно: {seiyu_link} для тайтла {url}")            

            # Выводим имена сейю через запятую
            seiyu_string = ', '.join(seiyu_list)
            if len(seiyu_list) > 0:
                print(f'Удалось найти китайских сейю для тайтла {url}, их {len(seiyu_list)}')

    except:
        seiyu_string = 'Не смог'
        print(f'Не смог получить строку(список) сейю для тайтла {url}')

    #Получение рейтинга тайтла
    try:
        score = soup.find('div', class_='text-score').text
        digits_only = re.sub(r'\D', '', score)
        rate = digits_only[:1] + '.' + digits_only[1:]
    except:
        rate = 'Не смог'
        print(f'Не смог получить рейтинг для тайтла {url}')

    data.append([anime_name, anime_type, episodes, episode_length, status, genres, themes, age_limit, studios, authors_string, related_list, description, seiyu_string, rate, url])

    #Обнуление переменных
    anime_name = None
    anime_type = None
    episodes = None
    episode_length = None
    status = None
    genres = None
    themes = None
    age_limit = None
    studios = None
    authors_string = None
    related_list = None
    description = None
    seiyu_string = None
    rate = None
    url = None

    


Элемент 1: Ссылка на аниме
Не удалось получить суп для Ссылка на аниме
Не смог получить строку(список) авторов(стафа) для тайтла Ссылка на аниме
Не смог получить информацию о смежных произведениях для тайтла Ссылка на аниме
Не смог получить строку(список) сейю для тайтла Ссылка на аниме
Элемент 2: https://shikimori.one/animes/52991-sousou-no-frieren
Элемент 3: https://shikimori.one/animes/z5114-fullmetal-alchemist-brotherhood
Элемент 4: https://shikimori.one/animes/z9253-steins-gate
Элемент 5: https://shikimori.one/animes/z28977-gintama
Элемент 6: https://shikimori.one/animes/38524-shingeki-no-kyojin-season-3-part-2
Элемент 7: https://shikimori.one/animes/39486-gintama-the-final
Элемент 8: https://shikimori.one/animes/z11061-hunter-x-hunter-2011
Элемент 9: https://shikimori.one/animes/41467-bleach-sennen-kessen-hen
Элемент 10: https://shikimori.one/animes/z9969-gintama
Элемент 11: https://shikimori.one/animes/820-ginga-eiyuu-densetsu
Элемент 12: https://shikimori.one/animes/z15417-gint

In [56]:
data

[['Сёва-Гэнроку: Двойное самоубийство по ракуго',
  'TV Сериал',
  '13',
  '26 мин',
  'вышло',
  ['Дзёсей', 'Драма'],
  ['Исторический', 'Любовный многоугольник', 'Исполнительское искусство'],
  'PG-13',
  ['Deen'],
  'Не смог',
  'Не смог',
  'Как должен жить человек, только что вышедший из тюрьмы? Что он собирается делать дальше, намеренно или случайно оступившись в прошлом? Какое будущее ему предначертано?Когда Ётаро отбывал свой срок в тюрьме, ему посчастливилось увидеть выступление одного знаменитого ракугоки, Якумо. Тогда этот рассказчик исполнил историю под названием «Синигами», которая глубоко вонзилась в сердце Ётаро. В тот момент парень по-настоящему осознал, что с этого момента ракуго — смысл его жизни, потому после освобождения сразу же отправился к Якумо, чтобы стать его учеником. Правда, этот рассказчик никогда ранее не брал никого в ученики, но, к всеобщему удивлению, он принял бывшего заключённого и дал ему место, где тот бы мог жить и учиться у своего новоиспечённого 

In [57]:
import pandas as pd

# ваш код для получения data

# Названия столбцов
columns = ['Title', 'Type', 'Episodes', 'Episode length', 'Status', 'Genres', 'Themes', 'Age Limit', 'Studios', 'Authors', 'Related', 'Description', 'Seiyu', 'Rate', 'Url']

# Создаем DataFrame из списка data
df = pd.DataFrame(data, columns=columns)
print(df)
# Сохраняем DataFrame в Excel
df.to_excel('anime_data.xlsx', index=False)


                                                  Title           Type  \
0          Сёва-Гэнроку: Двойное самоубийство по ракуго      TV Сериал   
1                   Провожающая в последний путь Фрирен      TV Сериал   
2                            Стальной алхимик: Братство      TV Сериал   
3                                          Врата Штейна      TV Сериал   
4                                             Гинтама 4      TV Сериал   
...                                                 ...            ...   
12976                                Повесть о Момоваро            ONA   
12977                                    Девчачья битва            OVA   
12978  Shouka Robo Zeres: Fire Dragon wo Taose!АнимеМех            OVA   
12979             Маленький лорд Фонтлерой: Спецвыпуски  TV Спецвыпуск   
12980                                     Мальчик Асибэ            OVA   

         Episodes Episode length   Status  \
0              13         26 мин    вышло   
1         26 / 28    